In [41]:
import pandas as pd
import pyomo.environ as pe
import pyomo.opt as po
from openpyxl import load_workbook
import os

# Initialize parameters
ninscope = 15
threshold_within = 1
threshold_among = 1

# Function to create Pyomo model
def create_model(ninscope, threshold_within, threshold_among):
    pathdemand = f"CleanInput/{ninscope}/discharge_{ninscope}.xlsx"
    pathhospitalbeds = f"CleanInput/{ninscope}/beds_{ninscope}.xlsx"
    pathdemandcluster = f"CleanInput/{ninscope}/dischargebycluster_{ninscope}.xlsx"

    drg = pd.read_excel("CleanInput/weight.xlsx", dtype={'DRGCode': 'string', 'ClusterId': 'string'})
    demand = pd.read_excel(pathdemand, dtype={'DRGCode': 'string'})
    demand_cluster = pd.read_excel(pathdemandcluster, dtype={'DRGCode': 'string', 'ClusterId': 'string'})
    hospitalbeds = pd.read_excel(pathhospitalbeds, dtype={'DRGCode': 'string'})

    drg_revenue = drg[['DRGCode', 'Revenue']]
    revenue = dict(drg_revenue.values)
    drg_cluster = drg[['DRGCode', 'ClusterId']]
    cluster = dict(drg_cluster.values)
    drg_LOS = drg[['DRGCode', 'MeanLOS']]
    LOS = dict(drg_LOS.values)
    area_discharge = demand[['Region', 'DRGCode', 'Discharge']]
    discharge = {(row['Region'], row['DRGCode']): row['Discharge'] for index, row in area_discharge.iterrows()}
    area_discharge_cluster = demand_cluster[['Region', 'ClusterId', 'Discharge']]
    discharge_cluster = {(row['Region'], row['ClusterId']): row['Discharge'] for index, row in
                         area_discharge_cluster.iterrows()}
    bedsday = dict(hospitalbeds.values)

    model = pe.ConcreteModel()
    model.D = pe.Set(initialize=revenue.keys(), ordered=False)
    model.S = pe.Set(initialize=bedsday.keys(), ordered=False)
    model.C = pe.Set(initialize=["1", "2", "3", "4", "5", "6"], ordered=False)
    model.n = pe.Var(model.S, model.D, domain=pe.NonNegativeIntegers)

    model.obj = pe.Objective(expr=sum(model.n[s, d] * revenue[d] for s in model.S for d in model.D), sense=pe.maximize)

    model.cnstr1 = pe.ConstraintList()
    for s in model.S:
        expression = sum(model.n[s, d] * LOS[d] for d in model.D) <= bedsday[s]
        model.cnstr1.add(expression)

    model.cnstr2 = pe.ConstraintList()
    for s in model.S:
        for i in model.D:
            for j in model.D:
                if i != j and discharge[s, i] > 0 and discharge[s, j] > 0 and cluster[i] == cluster[j]:
                    expression = (model.n[s, i] / discharge[s, i]) - (model.n[s, j] / discharge[s, j]) <= threshold_within
                    model.cnstr2.add(expression)

    model.cnstr3 = pe.ConstraintList()
    for u in model.C:
        for v in model.C:
            for s in model.S:
                if u != v and discharge_cluster[s, u] != 0 and discharge_cluster[s, v] != 0:
                    expression = (sum(model.n[s, i] for i in model.D if cluster[i] == u) / discharge_cluster[s, u]) - (
                                sum(model.n[s, j] for j in model.D if cluster[j] == v) / discharge_cluster[s, v]) <= threshold_among
                    model.cnstr3.add(expression)

    model.cnstr4 = pe.ConstraintList()
    for s in model.S:
        for i in model.D:
            expression = model.n[s, i] <= discharge[s, i]
            model.cnstr4.add(expression)

    return model


# Function to solve model and save results
def solve_model(model, ninscope, threshold_within, threshold_among):
    solver = po.SolverFactory('gurobi')
    result = solver.solve(model, tee=True, options={'TimeLimit': 1800}, report_timing=True)

    output = []
    for s in model.S:
        for d in model.D:
            if pe.value(model.n[s, d]) != 0:
                output.append({'Threshold_InGroup': threshold_within, 'Threshold_Among': threshold_among,
                               'Region': s, 'DRG': d, 'ProposedVolume': pe.value(model.n[s, d])})

    df = pd.DataFrame(output)
    folder_path = f"Output/{ninscope}"
    os.makedirs(folder_path, exist_ok=True)
    file_path = f"{folder_path}/output_{ninscope}-{threshold_within}-{threshold_among}.xlsx"
    df.to_excel(file_path, index=False)

    # Calculate Optimality Gap
    optimal_obj_value = result.problem.upper_bound
    best_obj_value = result.problem.lower_bound
    if optimal_obj_value != 0:
        optimality_gap = abs(best_obj_value - optimal_obj_value) / abs(optimal_obj_value) * 100
    else:
        optimality_gap = 0

    # Load the Excel file
    wb = load_workbook("Output/Revenue.xlsx")
    ws = wb.active
    non_blank_rows = [cell.row for cell in ws['A'] if cell.value is not None]

    # Write the value to the first blank cell in the column
    first_blank_row = max(non_blank_rows) + 1 if non_blank_rows else 1  # Find the first blank row
    ws[f"A{first_blank_row}"] = str(ninscope)
    ws[f"B{first_blank_row}"] = threshold_within
    ws[f"C{first_blank_row}"] = threshold_among
    ws[f"D{first_blank_row}"] = pe.value(model.obj)
    ws[f"E{first_blank_row}"] = result.solver.time
    ws[f"F{first_blank_row}"] = optimality_gap
    ws[f"G{first_blank_row}"] = result.solver.status
    ws[f"H{first_blank_row}"] = result.solver.termination_condition

    # Save the file
    wb.save("Output/Revenue.xlsx")


# Main loop
while ninscope <= 25:
    threshold_within = 1
    while threshold_within >= 0:
        threshold_among = 1
        while threshold_among >= 0:
            model = create_model(ninscope, threshold_within, threshold_among)
            solve_model(model, ninscope, threshold_within, threshold_among)
            threshold_among -= 0.1
            threshold_among = round(threshold_among, 1)
        threshold_within -= 0.1
        threshold_within = round(threshold_within, 1)
    ninscope += 1
    ninscope = round(ninscope, 1)



        7.16 seconds required to write file
        7.17 seconds required for presolve
Set parameter Username
Academic license - for non-commercial use only - expires 2025-02-04
Read LP format model from file /var/folders/8k/qczgzz1s1_sbr6qypb4q0c0w0000gp/T/tmp_8y789vd.pyomo.lp
Reading time = 1.59 seconds
x1: 1338036 rows, 11475 columns, 2783788 nonzeros
Set parameter TimeLimit to value 1800
Gurobi Optimizer version 11.0.0 build v11.0.0rc2 (mac64[arm] - Darwin 22.5.0 22F82)

CPU model: Apple M1
Thread count: 8 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 1338036 rows, 11475 columns and 2783788 nonzeros
Model fingerprint: 0x4c12f112
Variable types: 0 continuous, 11475 integer (0 binary)
Coefficient statistics:
  Matrix range     [4e-06, 4e+01]
  Objective range  [1e+03, 2e+05]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+00, 3e+06]
Found heuristic solution: objective 2.020378e+10
Presolve removed 1338021 rows and 3897 columns
Presolve ti